https://drive.google.com/file/d/1IJ2NkeFH3fL-PYhrAak5ujbuQrg4YFgA/view?usp=drive_link

<center> <b>Machine Learning - SBU FALL 2024</b></center> 

In [203]:
student_number = '400243082'
Name = 'Pouria'
Last_Name = 'Yazdani'

In this notebook, you are expected to implement a fully functional MLP (Multi-Layer Perceptron) neural network from scratch. 
You are not allowed to use any libraries (including numpy). You will use the **Iris dataset** for training and testing your network, focusing on reducing the error on this dataset. 


**modify iris dataset to a version compatible with this task : binary classifiaction of if a flower is setosa (1) or not(-1)**

# Automatic Differentiation

Automatic differentiation has two main methods: forward mode and reverse mode. 
PyTorch uses the reverse mode approach, and we will also use this method in this project.

To learn this concept, simply click on this [link](https://auto-ed.readthedocs.io/en/latest/mod3.html#i-the-basics-of-reverse-mode) 
and read only the section "Intuition for Example An IV" up to the end of step six.

Essentially, you need to consider a data structure to build a computational graph. 
By calling the `backward` function on the network's output, you can compute the derivative of the output 
with respect to all weights and biases of the network. (In this case, our network has only one output.)


## Visualization Tool

In [204]:
from graphviz import Digraph
import random
import math
from math import exp

def trace(root):
    nodes, edges = set(), set()

    def build(v):
        if v not in nodes:
            nodes.add(v)
            for child in v.children:
                edges.add((child, v))
                build(child)

    build(root)
    return nodes, edges


def draw_dot(root, format='svg', rankdir='LR'):
    """
    format: png | svg | ...
    rankdir: TB (top to bottom graph) | LR (left to right)
    """
    assert rankdir in ['LR', 'TB']
    nodes, edges = trace(root)
    dot = Digraph(format=format, graph_attr={'rankdir': rankdir})  # , node_attr={'rankdir': 'TB'})

    for n in nodes:
        dot.node(name=str(id(n)), label="{ %s | data %.4f | grad %.4f }" % (n.label, n.value, n.grad), shape='record')
        if n.operator:
            dot.node(name=str(id(n)) + n.operator, label=n.operator)
            dot.edge(str(id(n)) + n.operator, str(id(n)))

    for n1, n2 in edges:
        dot.edge(str(id(n1)), str(id(n2)) + n2.operator)

    return dot

## Tensor

In [205]:
class Tensor:

  def __init__(self, value, label='', children=(), operator=None):
    self.value = value
    self.children = set(children)
    self.operator = operator
    self.grad = 0
    self._backward = lambda  : None
    self.label = label


  def __repr__(self) -> str:
    return f"Tensor(label = {self.label}, value = {self.value}, grad = {self.grad}, operator = {self.operator})"

  # normal add
  def __add__(self, other):

    # ensure other is also a Tensor 
    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value + other.value
    out = Tensor(out_value, children=(self, other), operator='+')

    def backward():
      self.grad += 1 * out.grad 
      other.grad += 1 * out.grad

    out._backward = backward

    return out

  # reverse add
  def __radd__(self, other):
    return self + other # other is int or float -> 5.4 + Tensor(4.0, label='a') 

  def __sub__(self, other):
    # ensure other is also a Tensor 
    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value - other.value
    out = Tensor(out_value, children=(self, other), operator='-')

    def backward():
      self.grad += 1 * out.grad
      other.grad += -1 * out.grad

    out._backward = backward

    return out
  
  # def __rsub__(self, other):
  #   return -(self - other) # not commutative

  def __mul__(self, other):
    # ensure other is also a Tensor 
    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value * other.value
    out = Tensor(out_value, children=(self, other), operator='*')

    def backward():
      self.grad += (other.value) * out.grad
      other.grad += (self.value)* out.grad

    out._backward = backward

    return out


  def __rmul__(self, other):
    return self * other

  def __truediv__(self, other):
    # ensure other is also a Tensor 
    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value / other.value
    out = Tensor(out_value, children=(self, other), operator='/')

    def backward():
      self.grad += (1/other.value) * out.grad
      other.grad += -(self.value/(other.value**2)) * out.grad

    out._backward = backward

    return out

    

  def __pow__(self, other):
      # ensure other is also a Tensor 
    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value ** other.value
    out = Tensor(out_value, children=(self, other), operator='^')

    def backward():
      epsilon = 1e-10
      self.grad += (other.value*(self.value**(other.value-1))) * out.grad
      other.grad += (math.log(max(self.value, epsilon))*(self.value**other.value)) * out.grad #TODO log(0) handling


    out._backward = backward

    return out

  def backward(self): # loss Tensor is the root of all , weights and inputs are the leaf nodes
    # Build the computation graph from right side
    nodes_lr = []  # _lr means left to righ because the leaf nodes are inserted before their parents (loss is the root and is the last element in this list)
    visited = set() 

    def build_graph_rl(v):
        if v not in visited:
            visited.add(v)
            for child in v.children:
                build_graph_rl(child)
            nodes_lr.append(v)

    build_graph_rl(self)

    # d out/d_out = 1
    self.grad = 1.0

    # backprop 
    for node in reversed(nodes_lr): # start from loss ()
        if node._backward:
            node._backward()

# Activation Functions

In [206]:
class F:

  @staticmethod
  def tanh(x: Tensor) -> Tensor:
    """
        tanh(x) = (e^x - e^(-x)) / (e^x + e^(-x))
    """
    out_value = (math.exp(x.value) - math.exp(-x.value)) / (math.exp(x.value) + math.exp(-x.value))
    out = Tensor(out_value, children=(x,), operator='tanh')
    
    def backward():
      """
        Backward: tanh'(x) = 1 - tanh^2(x)
      """
      x.grad += (1 - out_value**2) * out.grad

    out._backward = backward

    return out

# Neuron, Layer & MLP (Forward Section)

In [237]:
from typing import List

class Neuron:

  def __init__(self, input_size):

    self.weights = [Tensor(random.uniform(-1, 1)) for i in range(input_size)]
    self.bias = Tensor(random.uniform(-1, 1))

  def forward(self, x:List[Tensor],activation=True): # single neuron -> scalar output
    weighted_sum = sum(w * xi for w, xi in zip(self.weights, x))
    if activation:
      return weighted_sum + self.bias
    else:
      return F.tanh(weighted_sum + self.bias)

  def __call__(self, x):
    return self.forward(x)

  def parameters(self):
    return self.weights + [self.bias]

  def __print__(self):
    weights_str = ', '.join(f"{w.value:.4f}" for w in self.weights)
    print(f"Neuron(weights=[{weights_str}], bias={self.bias.value:.4f})")

In [247]:
class Layer:

  def __init__(self, input_size, output_size):
    self.neurons = [Neuron(input_size) for _ in range(output_size)]

  def forward(self, x:List[Tensor], activation:bool) -> List:
    """
      returns a list with len=output_size=num_neurons (output dim)
    """
    return [neuron(x) for neuron in self.neurons]


  def __call__(self, x, activation=True):
    return self.forward(x,activation=activation)

  def parameters(self):
    return [param for neuron in self.neurons for param in neuron.parameters()]


  def __print__(self):
    for i, neuron in enumerate(self.neurons):
      print(f"Neuron {i+1}:")
      neuron.__print__()

# The MLP Class Structure

The `MLP` class is expected to have three main methods, which you should implement with the same structure:

1. **`forward` Method:**  
   This method performs calculations on the input and returns the output.

2. **`__call__` Method:**  
   This method simply calls the `forward` method. Essentially, we want to pass the input to the model in this way: `model(x)`.

3. **`parameters` Method:**  
   This method returns all the weights of the network in a list.

---

# Layers in the MLP

The `MLP` class itself consists of several layers (referred to as `Layer`), which are the actual layers of the neural network. Each layer needs to know:
- The dimensions of the input data.
- The dimensions of the output data.

In this project, all inputs are vectors. Each `Layer` consists of several neurons. For example:
- If a layer receives a 7-dimensional vector as input (input size) and produces a 4-dimensional vector as output, then:
  - The layer should have 4 neurons.
  - Each neuron should have 7 weights and 1 bias.

You should implement the details and structure of the layers and neurons according to the given explanation.


In [248]:
class MLP:

  def __init__(self, input_size:int, layer_sizes:list):
    """
      Each layer connects the previous layer's output size to the next layer's output size.
      Args:
      - layer_sizes: A list of integers where each element represents the number of neurons
                      in a layer which is essentially the output dimension of that layer.
    """
    layers_total = [input_size] + layer_sizes
    self.layers = [Layer(layers_total[i], layers_total[i+1]) for i in range(len(layer_sizes))]

  def forward(self, x:List[Tensor]) -> List[Tensor]:
    """
      performs forward pass throgh all layers of the MLP

      Returns:
      - output of the final layer as a list of Tensors.
    """
    for i, layer in enumerate(self.layers):# in each iteration x is the output of the previous layer
        if i == len(self.layers)-1: # last layer -> no activation
          x = layer(x,False)  
        else:
           x = layer(x)
    return x

  def __call__(self, x:List[Tensor]):
    return self.forward(x)

  def parameters(self)->List[Tensor]:
    """    
    Returns:
    - A list of all the weights and biases in the MLP.
    """
    return [param for layer in self.layers for param in layer.parameters()]

  def __print__(self):
    num_layers = len(self.layers)
    total_parameters_num = sum(len(layer.parameters()) for layer in self.layers)

    print("MLP Summary:")
    print(f"Total Number of Layers: {num_layers}")
    print(f"Total Number of Parameters: {total_parameters_num}")

    print("\nLayer Details:")
    for i, layer in enumerate(self.layers):
        layer_params = len(layer.parameters())
        input_size = len(layer.neurons[0].weights)  # Input size for this layer
        output_size = len(layer.neurons)  # Number of neurons (output size)
        print(f"  Layer {i + 1}:")
        print(f"    Shape: ({input_size} -> {output_size})")
        print(f"    Number of Parameters: {layer_params}")
        print()

    # Print detailed structure of each layer
    print("\nMLP Structure:")
    for i, layer in enumerate(self.layers):
        print(f"Layer {i + 1}:")
        layer.__print__()

# Optimizer

Similar to the first project, the `optimizer` should have access to the network's weights. 
This time, it must update them based on their derivatives and the value of the `lr` parameter (learning rate).

- **`step` Method:**  
  This method functions similarly to the `update` method in the previous project. It updates the weights of the network.

- **`grad_zero` Method:**  
  An additional method called `grad_zero` is included, whose functionality has been explained. It is used to reset the gradients of the weights to zero after each update step.


In [249]:
class Optimizer:
  def __init__(self, parameters, lr):
    self.parameters = parameters
    self.lr = lr

  def zero_grad(self):
    """ 
      reset the gradients of all parameters to zero
    """
    for param in self.parameters:
        param.grad = 0.0
  def step(self):
    """ 
      new_value = old_value - (lr * gradient)
    """
    for param in self.parameters:
        if param.grad is not None:  
            param.value -= self.lr * param.grad

# Training Part

Prepeare the dataset in this section in bellow code snippet we place a toy example dataset just for better clarification

In [250]:
from sklearn.datasets import load_iris

iris = load_iris()
iris_list = [[features]+[targets] for features, targets in zip(iris.data, iris.target)]

# print(iris.target_names) -> array(['setosa', 'versicolor', 'virginica'], dtype='<U10')

for row in iris_list:
    row.append(1 if row[-1] == 0 else -1) # make the target data suitbale for binary classifiation on setosa (setosa is target=0)

setosa_samples = [row for row in iris_list if row[-2] == 0] 
versicolor_samples = [row for row in iris_list if row[-2] == 1]
virginica_samples = [row for row in iris_list if row[-2] == 2]

# 30 15 15 samples of setosa versicolor and virginica (in order)
random.seed(42)
setosa_samples = random.sample(setosa_samples, 30)
versicolor_samples = random.sample(versicolor_samples, 15)
virginica_samples = random.sample(virginica_samples, 15)

dataset = setosa_samples + versicolor_samples + virginica_samples
random.shuffle(dataset)


X = [[Tensor(value) for value in row[0]] for row in dataset]
Y = [Tensor(row[-1]) for row in dataset] # list of Tensor scalars

print(X[0:4])
print(Y[0:4])


[[Tensor(label = , value = 5.4, grad = 0, operator = None), Tensor(label = , value = 3.9, grad = 0, operator = None), Tensor(label = , value = 1.7, grad = 0, operator = None), Tensor(label = , value = 0.4, grad = 0, operator = None)], [Tensor(label = , value = 5.0, grad = 0, operator = None), Tensor(label = , value = 3.5, grad = 0, operator = None), Tensor(label = , value = 1.3, grad = 0, operator = None), Tensor(label = , value = 0.3, grad = 0, operator = None)], [Tensor(label = , value = 7.7, grad = 0, operator = None), Tensor(label = , value = 2.8, grad = 0, operator = None), Tensor(label = , value = 6.7, grad = 0, operator = None), Tensor(label = , value = 2.0, grad = 0, operator = None)], [Tensor(label = , value = 5.1, grad = 0, operator = None), Tensor(label = , value = 2.5, grad = 0, operator = None), Tensor(label = , value = 3.0, grad = 0, operator = None), Tensor(label = , value = 1.1, grad = 0, operator = None)]]
[Tensor(label = , value = 1, grad = 0, operator = None), Tensor

In [251]:
X

[[Tensor(label = , value = 5.4, grad = 0, operator = None),
  Tensor(label = , value = 3.9, grad = 0, operator = None),
  Tensor(label = , value = 1.7, grad = 0, operator = None),
  Tensor(label = , value = 0.4, grad = 0, operator = None)],
 [Tensor(label = , value = 5.0, grad = 0, operator = None),
  Tensor(label = , value = 3.5, grad = 0, operator = None),
  Tensor(label = , value = 1.3, grad = 0, operator = None),
  Tensor(label = , value = 0.3, grad = 0, operator = None)],
 [Tensor(label = , value = 7.7, grad = 0, operator = None),
  Tensor(label = , value = 2.8, grad = 0, operator = None),
  Tensor(label = , value = 6.7, grad = 0, operator = None),
  Tensor(label = , value = 2.0, grad = 0, operator = None)],
 [Tensor(label = , value = 5.1, grad = 0, operator = None),
  Tensor(label = , value = 2.5, grad = 0, operator = None),
  Tensor(label = , value = 3.0, grad = 0, operator = None),
  Tensor(label = , value = 1.1, grad = 0, operator = None)],
 [Tensor(label = , value = 4.4, grad

## Loss Function (SE)

In [252]:
from typing import List

def criterion(y_hats: List[Tensor], Y) -> Tensor:
  return sum([(y_hat - y)**2 for y_hat, y in zip(y_hats, Y)]) / Tensor(len(Y))

## Training Loop

# Training Steps for the Model

1. **Calculate Model Predictions:**  
   For each input `x`, compute the output of the model, `y_hat`.

2. **Compute Error:**  
   Calculate the error of the predictions using the Mean Squared Error (MSE) loss function for simplicity.

3. **Reset Gradients of Network Variables:**  
   Set the gradients of all variables in the network to zero. Once you implement automatic differentiation, you will understand why this step is necessary.

4. **Compute Derivatives:**  
   This is the most challenging part of the project. When this function is called, you need to calculate the derivative of the `loss` with respect to all weights and biases of the network.  
   To implement this, you will use **Automatic Differentiation (AutoDiff)**.

5. **Update Network Weights:**  
   The `optimizer` will use the derivatives of the `loss` with respect to all weights and biases to update them in a direction that reduces the error in the next step.


In [253]:
def metrics(preds,Y):
  tp = sum([1 for p, y in zip(preds, Y) if p == 1 and y.value == 1])  # True positives
  tn = sum([1 for p, y in zip(preds, Y) if p == -1 and y.value == -1])  # True negatives
  fp = sum([1 for p, y in zip(preds, Y) if p == 1 and y.value == -1])  # False positives
  fn = sum([1 for p, y in zip(preds, Y) if p == -1 and y.value == 1])  # False negatives
  # Accuracy
  accuracy = (tp + tn) / len(Y)
  # Precision
  precision = tp / (tp + fp) if (tp + fp) > 0 else 0
  # Recall
  recall = tp / (tp + fn) if (tp + fn) > 0 else 0
  # F1 Score
  f1 = (2 * precision * recall) / (precision + recall) if (precision + recall) > 0 else 0
  return accuracy, precision, recall, f1
  
    

In [254]:
n_epochs = 20

input_size = 4 # Number of features in the input layer
layer_sizes = [2, 3, 1] # Number of neurons in each hidden and output layer
model = MLP(input_size, layer_sizes)
optimizer = Optimizer(model.parameters(), lr=0.005)  # optimizer with learning rate 0.01


for epoch in range(n_epochs):
  # Forward pass: Compute predictions for the entire dataset
  y_hats = [model(X[i])[-1] for i in range(len(X))]

  # Compute the loss
  loss = criterion(y_hats, Y)
  
  # Zero the gradients to prevent accumulation from previous iterations
  optimizer.zero_grad()

  # Backward pass: Compute the gradient of the loss function with respect to model parameters
  loss.backward()

  # Update the model parameters using the optimizer
  optimizer.step()
  # Calculate metrics
  preds = [1 if y_hat.value > 0 else -1 for y_hat in y_hats]
  accuracy, precision, recall, f1 = metrics(preds, Y)

  # Print metrics
  print(f"Epoch {epoch + 1}/{n_epochs}, Loss: {loss.value:.4f}, "
        f"Accuracy: {accuracy:.4f}, Precision: {precision:.4f}, Recall: {recall:.4f}, F1 Score: {f1:.4f}")


Epoch 1/20, Loss: 14.9435, Accuracy: 0.5000, Precision: 0.5000, Recall: 1.0000, F1 Score: 0.6667
Epoch 2/20, Loss: 0.9425, Accuracy: 0.5333, Precision: 0.5172, Recall: 1.0000, F1 Score: 0.6818
Epoch 3/20, Loss: 0.8763, Accuracy: 0.6833, Precision: 0.6122, Recall: 1.0000, F1 Score: 0.7595
Epoch 4/20, Loss: 0.8363, Accuracy: 0.7500, Precision: 0.6829, Recall: 0.9333, F1 Score: 0.7887
Epoch 5/20, Loss: 0.8054, Accuracy: 0.8667, Precision: 0.8235, Recall: 0.9333, F1 Score: 0.8750
Epoch 6/20, Loss: 0.7780, Accuracy: 0.9000, Precision: 0.9000, Recall: 0.9000, F1 Score: 0.9000
Epoch 7/20, Loss: 0.7522, Accuracy: 0.9333, Precision: 0.9333, Recall: 0.9333, F1 Score: 0.9333
Epoch 8/20, Loss: 0.7273, Accuracy: 0.9500, Precision: 0.9655, Recall: 0.9333, F1 Score: 0.9492
Epoch 9/20, Loss: 0.7029, Accuracy: 0.9500, Precision: 0.9655, Recall: 0.9333, F1 Score: 0.9492
Epoch 10/20, Loss: 0.6791, Accuracy: 0.9500, Precision: 0.9655, Recall: 0.9333, F1 Score: 0.9492
Epoch 11/20, Loss: 0.6556, Accuracy: 0

In [255]:
draw_dot(loss)